In [29]:
import warnings
from rpy2.rinterface import RRuntimeWarning
warnings.filterwarnings('ignore',category=FutureWarning)
warnings.filterwarnings('ignore',category=RRuntimeWarning)
import sys
import os

In [30]:
import pandas as pd
import numpy as np

In [31]:
from rpy2.robjects import pandas2ri
pandas2ri.activate()

In [32]:
# Enable R magic
%load_ext rpy2.ipython

The rpy2.ipython extension is already loaded. To reload it, use:
  %reload_ext rpy2.ipython


In [35]:
HERE = os.path.dirname(os.path.realpath('__file__'))
PROJECT = os.path.abspath(os.path.join(HERE, '..'))
DATA = os.path.join(PROJECT, 'data')

GENOTYPE_DATA = os.path.join(DATA, 'Asif_Genotype_Disease_Only_ROSMAP.csv')
SUGBRAPH_SNPS = os.path.join(DATA, 'subgraphs15_snps_mod1.csv')
SUBGRAPH_15_RDATA = os.path.join(DATA, 'subgraph15_snpset148.RData')

INPUT_FOR_MODEL = os.path.join(DATA, "rosmap148.snp.mat.RData")

AUTOENCODER_TRAINED_MATRIX = os.path.join(DATA, "autoencoder_trained_matrix.RData")
PATIENT_TRAINED_CLUSTERS = os.path.join(DATA, "trained_patient_clusters.RData")

In [6]:
%%R

library(h2o)
library(randomForest)
library(glmnet)
library(gbm)
library(bnlearn)
library(ggplot2)
library(CORElearn)
library(dplyr)
library(data.table)


R[write to console]: 
----------------------------------------------------------------------

Your next step is to start H2O:
    > h2o.init()

For H2O package documentation, ask for help:
    > ??h2o

After starting H2O, you can use the Web UI at http://localhost:54321
For more information visit http://docs.h2o.ai

----------------------------------------------------------------------


R[write to console]: 
Attache Paket: ‘h2o’


R[write to console]: The following objects are masked from ‘package:stats’:

    cor, sd, var


R[write to console]: The following objects are masked from ‘package:base’:

    %*%, %in%, &&, apply, as.factor, as.numeric, colnames, colnames<-,
    ifelse, is.character, is.factor, is.numeric, log, log10, log1p,
    log2, round, signif, trunc, ||


R[write to console]: randomForest 4.6-14

R[write to console]: Type rfNews() to see new features/changes/bug fixes.

R[write to console]: Lade nötiges Paket: Matrix

R[write to console]: Loaded glmnet 3.0-2


R[write

In [7]:
%%R
#### main function ####

ann_fun = function(input_data){
  if(dim(input_data)[2] > 1)
  {
    h2o.init(nthreads = -1, max_mem_size = "12g")
    
    #sc = scale(input_data)
    myx = as.h2o(scale(input_data)) 
    
    n = round(dim(input_data)[2])
    m = round(dim(input_data)[2]/2)
    
    hyper_params <- list(hidden = list(1, c(n, 1), c(n,m,1), c(m,1)),
                         input_dropout_ratio = c(0,0.05, 0.2,0.5),
                         l2=10^c(-4:4))
    
    
    r = sample(20:60000, 1)
 
  grid = h2o.grid("deeplearning", 
                    grid_id = paste("mygrid", r, sep="_"), 
                    autoencoder= TRUE,
                  x = colnames(myx),
                    training_frame = myx, 
                    seed=1234567, 
                    stopping_metric="MSE", 
                    stopping_rounds = 5,
                    #activation= "TanhWithDropout",
                    activation= "Tanh",
                    standardize=TRUE,
                    epochs=500,
                    hyper_params = hyper_params)
    
    gbm_sorted_grid <- h2o.getGrid(grid_id = paste("mygrid", r, sep="_"), sort_by = "mse")
    fit <- h2o.getModel(gbm_sorted_grid@model_ids[[1]])
    #nlayers = length(strsplit(gbm_sorted_grid@summary_table[1,1], ",")[[1]])
    #browser()
    nlayers = length(strsplit(substr(gbm_sorted_grid@summary_table[1,1], 2, nchar(gbm_sorted_grid@summary_table[1,1])-1), ",")[[1]])
    newvar = as.data.frame(h2o.deepfeatures(fit, myx, nlayers))
 
  
    #Rename column
 
    newvar = as.data.frame(newvar[,1])
    colnames(newvar) = paste( sub("_.*", '', colnames(input_data)[1]) , sub(".*_", '',colnames(input_data)[1]) , sep= "_")
    
   
    #save meta-features in variable 
    subgraph_feature = data.frame(matrix(NA, nrow = 194, ncol = 1)) #SNP data shape
    # subgraph_feature = data.frame(matrix(NA, nrow = 486, ncol = 1)) #SNP Data shape 
    colnames(subgraph_feature) = "dummy"
 
  
    subgraph_feature = cbind(subgraph_feature,newvar) 
    subgraph_feature$dummy = NULL
    
  }else if(dim(input_data)[2] == 1 ){
    subgraph_feature = as.data.frame(input_data)
    colnames(newvar) = paste( sub("_.*", '', colnames(input_data)[1]) , sub(".*_", '',colnames(input_data)[1]) , sep= "_")
  }else{
    subgraph_feature = data.frame(matrix(NA, nrow = 194, ncol = 1)) #844
    # subgraph_feature = data.frame(matrix(NA, nrow = 486, ncol = 1)) #844
    colnames(subgraph_feature) = "dummy"
  }
  outcome = list(subgraph_feature, fit) # scales=attributes(sc)
  return(outcome)
  #return(subgraph_feature)
}

In [8]:
# snps_data = pd.read_csv(GENOTYPE_DATA, index_col=0)
# snps_data = snps_data.transpose()

In [9]:
%%R -i=SUBGRAPH_15_RDATA,GENOTYPE_DATA,INPUT_FOR_MODEL

load(SUBGRAPH_15_RDATA)
userSNPs <- read.csv(GENOTYPE_DATA, row.names = 1, stringsAsFactors=FALSE)
userSNPs <- as.data.frame(t(userSNPs), stringsAsFactors = FALSE)

snp_mat = list()
k = 1
for (i in subgraph15.snps){
  snp_mat[[k]] = select(userSNPs, i)
  k = k + 1
}

names(snp_mat) <- names(subgraph15.snps)
save(snp_mat,file = INPUT_FOR_MODEL)


In [10]:
# snps_data.head()

In [12]:
# snps_data.shape

In [13]:
# snps_list = pd.read_csv(
#     SUGBRAPH_SNPS,header=None, index_col=0
# )

# subgraph2snps = {
#     index: snps.dropna().tolist()
#     for index, snps in snps_list.iterrows()
# }

Dictionary of subgraphs to dataframe slices for the SNPs in the subgraph

In [14]:
# snp_mat = [
#     snps_data[snps]
#     for _, snps in subgraph2snps.items()
# ]
# subgraph_4 = pandas2ri.py2rpy_pandasdataframe(snp_mat['Subgraph_4'])

In [16]:
%%R
# see: https://ipython.org/ipython-doc/2/config/extensions/rmagic.html

# apply main function on each mechanisms matrices
model.store <- lapply(snp_mat, function(x) ann_fun(x))

####### This does not work to apply for each subgraph #######
#model.store <- lapply(subgraph_4, function(x) ann_fun(x))
                      
# Stores the model
# save(model.store, file = "model.store.rosmapIdibaps-148_full.RData")


autoen=matrix(nrow = 194, ncol = 15) # 358 PD patients and 15 subgraphs

j=1
for (i in model.store){
  autoen[,j]=i[[1]][[1]]
  j=j+1
}



H2O is not running yet, starting it now...

Note:  In case of errors look at the following log files:
    /var/folders/yx/ppwbtpyn61l2796mnr1t62f00000gn/T//RtmpqcZMqn/h2o_danieldomingo_started_from_r.out
    /var/folders/yx/ppwbtpyn61l2796mnr1t62f00000gn/T//RtmpqcZMqn/h2o_danieldomingo_started_from_r.err


Starting H2O JVM and connecting: . Connection successful!

R is connected to the H2O cluster: 
    H2O cluster uptime:         2 seconds 286 milliseconds 
    H2O cluster timezone:       Europe/Berlin 
    H2O data parsing timezone:  UTC 
    H2O cluster version:        3.26.0.2 
    H2O cluster version age:    5 months and 24 days !!! 
    H2O cluster name:           H2O_started_from_R_danieldomingo_ekm683 
    H2O cluster total nodes:    1 
    H2O cluster total memory:   10.67 GB 
    H2O cluster total cores:    4 
    H2O cluster allowed cores:  4 
    H2O cluster healthy:        TRUE 
    H2O Connection ip:          localhost 
    H2O Connection port:        54321 
    H2O Conn

Hyper-parameter: hidden, 13
 Hyper-parameter: hidden, 1
Hyper-parameter: input_dropout_ratio, 0.5
Hyper-parameter: l2, 1000
[2020-01-20 10:17:33] failure_details: DistributedException from localhost/127.0.0.1:54321: '

Trying to predict with an unstable model.
Job was aborted due to observed numerical instability (exponential growth).
Either the weights or the bias values are unreasonably large or lead to large activation values.
Try a different initial distribution, a bounded activation function (Tanh), adding regularization
(via max_w2, l1, l2, dropout) or learning rate (either enable adaptive_rate or use a smaller learning rate or faster annealing).

For more information visit:
  http://jira.h2o.ai/browse/TN-4' 
[2020-01-20 10:17:33] failure_stack_traces: DistributedException from localhost/127.0.0.1:54321: '

Trying to predict with an unstable model.
Job was aborted due to observed numerical instability (exponential growth).
Either the weights or the bias values are unreasonably la

Hyper-parameter: hidden, 26
 Hyper-parameter: hidden, 13
 Hyper-parameter: hidden, 1
Hyper-parameter: input_dropout_ratio, 0.05
Hyper-parameter: l2, 10000
[2020-01-20 10:17:34] failure_details: DistributedException from localhost/127.0.0.1:54321: '

Trying to predict with an unstable model.
Job was aborted due to observed numerical instability (exponential growth).
Either the weights or the bias values are unreasonably large or lead to large activation values.
Try a different initial distribution, a bounded activation function (Tanh), adding regularization
(via max_w2, l1, l2, dropout) or learning rate (either enable adaptive_rate or use a smaller learning rate or faster annealing).

For more information visit:
  http://jira.h2o.ai/browse/TN-4' 
[2020-01-20 10:17:34] failure_stack_traces: DistributedException from localhost/127.0.0.1:54321: '

Trying to predict with an unstable model.
Job was aborted due to observed numerical instability (exponential growth).
Either the weights or the 

Hyper-parameter: hidden, 1
Hyper-parameter: input_dropout_ratio, 0.2
Hyper-parameter: l2, 10000
[2020-01-20 10:17:34] failure_details: DistributedException from localhost/127.0.0.1:54321: '

Trying to predict with an unstable model.
Job was aborted due to observed numerical instability (exponential growth).
Either the weights or the bias values are unreasonably large or lead to large activation values.
Try a different initial distribution, a bounded activation function (Tanh), adding regularization
(via max_w2, l1, l2, dropout) or learning rate (either enable adaptive_rate or use a smaller learning rate or faster annealing).

For more information visit:
  http://jira.h2o.ai/browse/TN-4' 
[2020-01-20 10:17:34] failure_stack_traces: DistributedException from localhost/127.0.0.1:54321: '

Trying to predict with an unstable model.
Job was aborted due to observed numerical instability (exponential growth).
Either the weights or the bias values are unreasonably large or lead to large activat

Hyper-parameter: hidden, 26
 Hyper-parameter: hidden, 13
 Hyper-parameter: hidden, 1
Hyper-parameter: input_dropout_ratio, 0.2
Hyper-parameter: l2, 10000
[2020-01-20 10:17:34] failure_details: DistributedException from localhost/127.0.0.1:54321: '

Trying to predict with an unstable model.
Job was aborted due to observed numerical instability (exponential growth).
Either the weights or the bias values are unreasonably large or lead to large activation values.
Try a different initial distribution, a bounded activation function (Tanh), adding regularization
(via max_w2, l1, l2, dropout) or learning rate (either enable adaptive_rate or use a smaller learning rate or faster annealing).

For more information visit:
  http://jira.h2o.ai/browse/TN-4' 
[2020-01-20 10:17:34] failure_stack_traces: DistributedException from localhost/127.0.0.1:54321: '

Trying to predict with an unstable model.
Job was aborted due to observed numerical instability (exponential growth).
Either the weights or the b

...

Hyper-parameter: hidden, 4
 Hyper-parameter: hidden, 1
Hyper-parameter: input_dropout_ratio, 0.5
Hyper-parameter: l2, 10000
[2020-01-20 10:29:34] failure_details: DistributedException from localhost/127.0.0.1:54321: '

Trying to predict with an unstable model.
Job was aborted due to observed numerical instability (exponential growth).
Either the weights or the bias values are unreasonably large or lead to large activation values.
Try a different initial distribution, a bounded activation function (Tanh), adding regularization
(via max_w2, l1, l2, dropout) or learning rate (either enable adaptive_rate or use a smaller learning rate or faster annealing).

For more information visit:
  http://jira.h2o.ai/browse/TN-4' 
[2020-01-20 10:29:34] failure_stack_traces: DistributedException from localhost/127.0.0.1:54321: '

Trying to predict with an unstable model.
Job was aborted due to observed numerical instability (exponential growth).
Either the weights or the bias values are unreasonably la

Hyper-parameter: hidden, 8
 Hyper-parameter: hidden, 1
Hyper-parameter: input_dropout_ratio, 0
Hyper-parameter: l2, 100
[2020-01-20 10:29:34] failure_details: DistributedException from localhost/127.0.0.1:54321: '

Trying to predict with an unstable model.
Job was aborted due to observed numerical instability (exponential growth).
Either the weights or the bias values are unreasonably large or lead to large activation values.
Try a different initial distribution, a bounded activation function (Tanh), adding regularization
(via max_w2, l1, l2, dropout) or learning rate (either enable adaptive_rate or use a smaller learning rate or faster annealing).

For more information visit:
  http://jira.h2o.ai/browse/TN-4' 
[2020-01-20 10:29:34] failure_stack_traces: DistributedException from localhost/127.0.0.1:54321: '

Trying to predict with an unstable model.
Job was aborted due to observed numerical instability (exponential growth).
Either the weights or the bias values are unreasonably large 

  |======================================================================| 100%


R[write to console]: Fehler in rownames(snp.mat[[1]]) : objeto 'snp.mat' no encontrado
Ruft auf: <Anonymous> -> <Anonymous> -> withVisible -> rownames

R[write to console]: Además: 
R[write to console]: Es gab 15 Warnungen (Anzeige mit warnings())
R[write to console]: 




Fehler in rownames(snp.mat[[1]]) : objeto 'snp.mat' no encontrado
Ruft auf: <Anonymous> -> <Anonymous> -> withVisible -> rownames


In [18]:
%%R
#' save models in h2o format

rownames(autoen) <- rownames(snp_mat[[1]])
colnames(autoen) <- names(model.store)
save(autoen, file = "autoen_matrix_rosmapIdibaps-148_full.RData")

an_model <- lapply(model.store, '[[',2)  # This returns a list with only the 2nd element (h2o models)

# for (i in an_model){
#   h2o.saveModel(i, path = "autoen_rosmapIdibaps-148_h2omodel_full/")
# }

h2o.shutdown(prompt = FALSE)
gc()


        [,1]  [,2]    [,3]  [,4]  [,5]    [,6]  [,7]
[1,] 1916309 102.4 3847231 205.5    NA 3847231 205.5
[2,] 3684206  28.2 8388608  64.0 16384 6154576  47.0


In [36]:
%%R -i=AUTOENCODER_TRAINED_MATRIX

### Start up a 1-node H2O server on the local machine, and allow it to use all CPU cores and up to 6GB of memory:
h2o.init(nthreads=-1, min_mem_size="6G")

### Import autoencoder data set #subgraph15
load(AUTOENCODER_TRAINED_MATRIX)
main_data <- data.frame(autoen)

#### read the cluster assignments of each patients
load(TRAINED_PATIENT_CLUSTERS)
rownames(clusters) <- clusters[,1]
clusters[,1] <- NULL


##### merge cluster assignment to the dataset
fin_data <- merge(clusters,main_data,by="row.names")
fin_data$clusters <- as.factor(fin_data$clusters)
rownames(fin_data) = fin_data$Row.names
fin_data <- fin_data[,-1]
fullD <- as.h2o(fin_data) # get complete data set into h2o frame for cross validation approach

##### Training Classifier

y = "clusters" # response variable
#x = names(trainData)
x = names(fullD)
x = x[-which(x==y)] # predictor variables

### Train Model
snpModel = h2o.glm(training_frame = fullD, 
                   #training_frame = trainD, # keep it commented while using cross validation
                   #validation_frame = validD, # keep it commented while using cross validation
                   x = x, 
                   y = y,
                   nfolds = 10, 
                   family='multinomial',
                   solver='L_BFGS',
                   lambda_search=TRUE)

print(snpModel)
h2o.performance(snpModel, xval = TRUE)
#h2o.saveModel(snpModel,path="/home/memon/genetic_analyses/ann/output/subgraph15/classifier_adpd_ann30")

#### Now predict the Test Data with the trained model #####
#snpModel = h2o.loadModel("/home/memon/genetic_analyses/ann/output/subgraph15/classifier_adpd_ann30/GLM_model_R_1552061363922_1")

 Connection successful!

R is connected to the H2O cluster: 
    H2O cluster uptime:         9 minutes 11 seconds 
    H2O cluster timezone:       Europe/Berlin 
    H2O data parsing timezone:  UTC 
    H2O cluster version:        3.26.0.2 
    H2O cluster version age:    5 months and 24 days !!! 
    H2O cluster name:           H2O_started_from_R_danieldomingo_gok171 
    H2O cluster total nodes:    1 
    H2O cluster total memory:   5.68 GB 
    H2O cluster total cores:    4 
    H2O cluster allowed cores:  4 
    H2O cluster healthy:        TRUE 
    H2O Connection ip:          localhost 
    H2O Connection port:        54321 
    H2O Connection proxy:       NA 
    H2O Internal Security:      FALSE 
    H2O API Extensions:         Amazon S3, XGBoost, Algos, AutoML, Core V3, Core V4 
    R Version:                  R version 3.6.2 (2019-12-12) 



R[write to console]: Fehler in load(AUTOENCODER_TRAINED_MATRIX) : 
  número mágico de archivo de restauración inválido (el archivo puede estar dañado) -- ningún dato recargado
Ruft auf: <Anonymous> -> <Anonymous> -> withVisible -> load

R[write to console]: Además: 
R[write to console]: Warnmeldungen:

R[write to console]: 1: 
R[write to console]: In h2o.clusterInfo() :
R[write to console]:  
Your H2O cluster version is too old (5 months and 24 days)!
Please download and install the latest version from http://h2o.ai/download/

R[write to console]: 2: 
R[write to console]: In grepl("RD[ABX][2-9]\n", magic) :
R[write to console]: 
 
R[write to console]:  string de entrada 1 es inválida en este locale

R[write to console]: 3: 
R[write to console]: In grepl("RD[ABX][2-9]\r", magic) :
R[write to console]: 
 
R[write to console]:  string de entrada 1 es inválida en este locale




Fehler in load(AUTOENCODER_TRAINED_MATRIX) : 
  número mágico de archivo de restauración inválido (el archivo puede estar dañado) -- ningún dato recargado
Ruft auf: <Anonymous> -> <Anonymous> -> withVisible -> load


From cffi callback <function _consolewrite_ex at 0x10bc38170>:
Traceback (most recent call last):
  File "/Library/Frameworks/Python.framework/Versions/3.7/lib/python3.7/site-packages/rpy2/rinterface_lib/callbacks.py", line 128, in _consolewrite_ex
    s = conversion._cchar_to_str_with_maxlen(buf, maxlen=n)
  File "/Library/Frameworks/Python.framework/Versions/3.7/lib/python3.7/site-packages/rpy2/rinterface_lib/conversion.py", line 111, in _cchar_to_str_with_maxlen
    s = ffi.string(c, maxlen).decode('utf-8')
UnicodeDecodeError: 'utf-8' codec can't decode byte 0xfc in position 66: invalid start byte
